<a href="https://colab.research.google.com/github/BrianKEverett/County-Line/blob/main/PS3_Everett_cleaner.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
#---------------------------SETUP----------------------------------
#get useful libraries
import time, os, sys, re #basics
import zipfile, json, datetime, string   #string for annotating points in scatter
import numpy as np #basic math
from statistics import * #stats

import matplotlib.pyplot as plt #import pylab as plt #apparently discouraged now:
 #https://stackoverflow.com/questions/11469336/what-is-the-difference-between-pylab-and-pyplot
 #https://www.tutorialspoint.com/matplotlib/matplotlib_pylab_module.htm

import pandas as pd
import pandas_datareader as pdr
from pandas_datareader import wb
from pandas.io.formats.style import Styler
#s4 = Styler(df4, uuid_len=0, cell_ids=False)

from google.colab import files

#import webbrowser

import seaborn as sns

from google.colab import data_table
data_table.enable_dataframe_formatter() #this enables spreadsheet view upon calling dataframe (without() )
data_table.max_columns = 50
#!and may have to click at top right spreadsheet icon

#many tricks how to extend notebook functionality
#https://coderzcolumn.com/tutorials/python/list-of-useful-magic-commands-in-jupyter-notebook-lab
#will display all output not just last command
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

#MAGICS and THEMES/STYLES: important! does affect not just shading/colors, but also fonts, spacing, etc
#(even if you only select default (v not selecting anything) [but does seem to work better if you do make explicit sleections])

###magics: https://ipython.readthedocs.io/en/stable/interactive/magics.html
#most essential setup for vis: it does affect vis! careful!! stick with inline, maybe notebook; others mostly for non-notebook, eg spyder environ
#https://jakevdp.github.io/PythonDataScienceHandbook/04.00-introduction-to-matplotlib.html recomends *inline*!
#show current one:
#%matplotlib
#%matplotlib --list
#interactive plots:
#%matplotlib notebook
#static images of your plot:
%matplotlib inline
#may play with this one and other magics (btw default is probably agg)
#%matplotlib nbagg

###themes/styles: https://matplotlib.org/stable/gallery/style_sheets/style_sheets_reference.html
#https://jakevdp.github.io/PythonDataScienceHandbook/04.11-settings-and-stylesheets.html
#https://matplotlib.org/stable/tutorials/introductory/customizing.html
#here more about art and style than under the hood functionality as with magics, explore and experiment
#many may find 'default' or seaborn ones more pleasing; my fav 'classic' is back from 90s ;)
#plt.style.available #list available styles :) may install more
#plt.style.use('default') # more delicate subtle than classic
plt.style.use('classic')  #  'seaborn-whitegrid' 'seaborn-white' 'seaborn-poster'
# btw: magics v theme/style sequence matters, eg if i specify classic style before inline magic, i wouldnt get grey bounding box im getting

**Note to self - add text below to describe the purpose of each data set. What is it? **

In [2]:
a=pd.read_csv("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Permits.csv")
b=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Taxes.csv")
c=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Overburdened_Communities_under_the_New_Jersey_Environmental_Justice_Law_2021.csv")
d=!wget -q -O d.xlsx https://github.com/BrianKEverett/County-Line/raw/main/2020_Uniform_Crime_Report.xlsx
e=!wget -q -O e.xlsx https://github.com/BrianKEverett/County-Line/raw/main/UninsuredCrude11_.xls

In [3]:
a['c']=a['DCA MUNI CODE'].astype(str)
a['c1']=a['c'].str[:-2]
a[['DCA MUNI CODE','c1']]

DCA MUNI CODE  c1
0               101   1
1               101   1
2               102   1
3               102   1
4               102   1
...             ...  ..
9778           2121  21
9779           2122  21
9780           2122  21
9781           2122  21
9782           2122  21

[9783 rows x 2 columns]

In [4]:
a = a.rename(columns={'DCA MUNI CODE': 'DCA'})
a.dtypes

ID                   int64
TAX CODE             int64
BLOCK NUMBER        object
LOT NUMBER          object
PAMS PIN            object
DCA                  int64
MUNICIPALITY        object
USE GROUP           object
Use Group Label     object
DATE ISSUED         object
TYPE                object
WORK VALUE          object
YCOORD             float64
XCOORD             float64
MATCH TYPE          object
c                   object
c1                  object
dtype: object

In [5]:
b = b.rename(columns={'County': 'COUNTY'})
b.dtypes

COUNTY           object
Municipality     object
DLGS Code         int64
LD                int64
CD                int64
BudgetTwenty      int64
MTRTwenty       float64
dtype: object

In [6]:
c = c.rename(columns={'MUN_CODE': 'DCA'})
c.dtypes

OBJECTID                            int64
GEOID                              object
POVUNIVERSE                         int64
POPUNDER2XPOV                       int64
LOW_INCOME_PCT                    float64
TOTALPOP                            int64
NONHISPWHITE                        int64
TOTALMINORITY                       int64
MINORITY_PCT                      float64
TOTHH                               int64
TOTLANGUAGEISO                      int64
PCTLINGUAGEISO                    float64
OVERBURDENED_COMMUNITY_CRITERI     object
BG_TRIBAL                          object
GEOID_COUNTYSUBDIVISION             int64
COUNTY                             object
NAME                               object
DCA                                 int64
SPLIT_BG                           object
SPLIT_MUN                          object
GLOBALID                           object
Shape__Area                       float64
Shape__Length                     float64
dtype: object

In [7]:
a

ID  TAX CODE BLOCK NUMBER LOT NUMBER          PAMS PIN   DCA  \
0        1       101          236       2.01     0101_236_2.01   101   
1        2       101         9.02       3.01    0101_9.02_3.01   101   
2        3       102            1        146        0102_1_146   102   
3        4       102            1        146        0102_1_146   102   
4        5       102            1         42         0102_1_42   102   
...    ...       ...          ...        ...               ...   ...   
9778  9911      2121           28          2         2121_28_2  2121   
9779  9912      2122        40.04      12.05  2122_40.04_12.05  2122   
9780  9913      2122           43          8         2122_43_8  2122   
9781  9914      2122           46         13        2122_46_13  2122   
9782  9915      2122           65          4         2122_65_4  2122   

         MUNICIPALITY USE GROUP  \
0        ABSECON CITY         M   
1        ABSECON CITY         E   
2       ATLANTIC CITY       A-2   
3       ATLANTIC CITY       R-5   
4       ATLANTIC CITY       A-3   
...               ...       ...   
9778  WASHINGTON BORO       R-5   
9779   WASHINGTON TWP       R-5   
9780   WASHINGTON TWP         E   
9781   WASHINGTON TWP         B   
9782   WASHINGTON TWP         B   

                                        Use Group Label DATE ISSUED TYPE  \
0                                            Mercantile     1/31/22  NEW   
1                                           Educational     5/19/22  ALT   
2     Clubs, Dance Halls, Casinos, Restaurants, Tave...     2/11/22  ALT   
3                      Residential (1 & 2 Family Homes)      2/7/22  ALT   
4       Churches, Libraries, Arcades, Comm. Halls, Gyms      6/2/22  ALT   
...                                                 ...         ...  ...   
9778                   Residential (1 & 2 Family Homes)     5/10/22  ALT   
9779                   Residential (1 & 2 Family Homes)     4/19/22  ALT   
9780                                        Educational     3/28/22  ALT   
9781                                           Business      7/7/22  ALT   
9782                                           Business     4/26/22  ALT   

     WORK VALUE    YCOORD    XCOORD                        MATCH TYPE     c  \
0       695,000  39.42626 -74.50651           Geocoded MOD-IV Address   101   
1     4,000,000  39.43838 -74.49508  MODIV Parcel Centroid Coordinate   101   
2     2,100,000  39.35812 -74.41946  MODIV Parcel Centroid Coordinate   102   
3     2,100,000  39.35812 -74.41946  MODIV Parcel Centroid Coordinate   102   
4       337,400  39.34857 -74.44706  MODIV Parcel Centroid Coordinate   102   
...         ...       ...       ...                               ...   ...   
9778  1,000,000  40.76098 -74.97956  MODIV Parcel Centroid Coordinate  2121   
9779    426,124  40.76882 -74.97339           Geocoded MOD-IV Address  2122   
9780    742,000  40.76709 -74.95510  MODIV Parcel Centroid Coordinate  2122   
9781    276,000  40.76168 -74.96144  MODIV Parcel Centroid Coordinate  2122   
9782    515,000  40.73557 -74.97370  MODIV Parcel Centroid Coordinate  2122   

      c1  
0      1  
1      1  
2      1  
3      1  
4      1  
...   ..  
9778  21  
9779  21  
9780  21  
9781  21  
9782  21  

[9783 rows x 17 columns]

In [8]:
#ac = pd.merge(a, c, how='left', on=['DCA'],indicator=True) #outer=keep all
#this was previous command in earlier version of PS3, but for this data it makes more sense to merge via Many:1, but first, advice is to first begin with a 1:1 merge

# can also use loc or iloc to subset/slice on both rows and cols
#auto.iloc[0:3,0] #first three rows, 1st var
#auto.loc[:, 'make':'weight']
#subsetting on condition
#auto.make[auto.mpg<15]
a.query("DCA >400 & DCA <438")

ID  TAX CODE BLOCK NUMBER LOT NUMBER       PAMS PIN  DCA  \
2125  2152       401          103          1     0401_103_1  401   
2126  2153       401          131         19    0401_131_19  401   
2127  2154       401          132          1     0401_132_1  401   
2128  2155       403          106       2.04  0403_106_2.04  403   
2129  2156       404       173.02          2  0404_173.02_2  404   
...    ...       ...          ...        ...            ...  ...   
2386  2420       436         6406          4    0436_6406_4  436   
2387  2421       436         6406          4    0436_6406_4  436   
2388  2422       436         8401          6    0436_8401_6  436   
2389  2423       436         8903         16   0436_8903_16  436   
2390  2424       436         8903         16   0436_8903_16  436   

         MUNICIPALITY USE GROUP                   Use Group Label DATE ISSUED  \
2125     AUDUBON BORO         E                       Educational     7/18/22   
2126     AUDUBON BORO       R-5  Residential (1 & 2 Family Homes)     8/22/22   
2127     AUDUBON BORO         E                       Educational     7/18/22   
2128  BARRINGTON BORO       R-5  Residential (1 & 2 Family Homes)      3/8/22   
2129    BELLMAWR BORO         B                          Business     5/31/22   
...               ...       ...                               ...         ...   
2386      WINSLOW TWP         B                          Business     7/29/22   
2387      WINSLOW TWP         B                          Business    12/20/22   
2388      WINSLOW TWP       R-5  Residential (1 & 2 Family Homes)      2/9/22   
2389      WINSLOW TWP       S-2                           Storage     6/21/22   
2390      WINSLOW TWP       S-2                           Storage     8/30/22   

     TYPE WORK VALUE    YCOORD    XCOORD                        MATCH TYPE  \
2125  ALT    626,000  39.88829 -75.07322  MODIV Parcel Centroid Coordinate   
2126  ADD    278,000  39.88294 -75.07717  MODIV Parcel Centroid Coordinate   
2127  ALT  1,173,450  39.88403 -75.07608  MODIV Parcel Centroid Coordinate   
2128  NEW    638,950  39.88225 -75.04595  MODIV Parcel Centroid Coordinate   
2129  ALT    912,625  39.86292 -75.08932           Geocoded MOD-IV Address   
...   ...        ...       ...       ...                               ...   
2386  ALT  1,067,973  39.68175 -74.88245  MODIV Parcel Centroid Coordinate   
2387  ALT    475,000  39.68175 -74.88245  MODIV Parcel Centroid Coordinate   
2388  NEW    288,060  39.64878 -74.84430           Geocoded MOD-IV Address   
2389  NEW    588,700  39.62255 -74.86188  MODIV Parcel Centroid Coordinate   
2390  ALT    439,296  39.62255 -74.86188  MODIV Parcel Centroid Coordinate   

        c c1  
2125  401  4  
2126  401  4  
2127  401  4  
2128  403  4  
2129  404  4  
...   ... ..  
2386  436  4  
2387  436  4  
2388  436  4  
2389  436  4  
2390  436  4  

[266 rows x 17 columns]

Doing the above subsetting to try and limit the data to just Camden County for the purpose of the Problem Set. This way, hopeful the data is Simplified.

In [9]:
b

COUNTY      Municipality  DLGS Code  LD  CD  BudgetTwenty  MTRTwenty
0   Burlington       Maple Shade        319   6   1          1026       0.82
1   Burlington           Palmyra        327   7   1          1238       1.18
2       Camden           Audubon        401   5   1          1335       0.87
3       Camden      Audubon Park        402   5   1          1109       3.72
4       Camden        Barrington        403   5   1          1357       1.18
5       Camden          Bellmawr        404   5   1          1364       1.13
6       Camden            Berlin        405   8   1          1275       0.79
7       Camden        Berlin Twp        406   6   1          1901       1.20
8       Camden         Brooklawn        407   5   1          1980       1.68
9       Camden            Camden        408   5   1          2519       1.55
10      Camden       Cherry Hill        409   6   1          1044       0.48
11      Camden       Chesilhurst        410   4   1          2148       1.80
12      Camden         Clementon        411   4   1          1261       1.60
13      Camden      Collingswood        412   6   1          1420       0.98
14      Camden         Gibbsboro        413   6   1          1554       0.88
15      Camden   Gloucester City        414   5   1          1838       2.30
16      Camden    Gloucester Twp        415   4   1          1067       1.13
17      Camden    Haddon Heights        418   5   1          1151       0.72
18      Camden        Haddon Twp        416   6   1           967       0.65
19      Camden       Haddonfield        417   6   1          1722       0.47
20      Camden          Hi-Nella        419   6   1          1112       1.48
21      Camden    Laurel Springs        420   4   1          1767       1.64
22      Camden          Lawnside        421   5   1          1745       0.95
23      Camden        Lindenwold        422   4   1           969       1.67
24      Camden          Magnolia        423   5   1          1381       1.03
25      Camden     Merchantville        424   6   1          1358       1.25
26      Camden     Mount Ephraim        425   5   1          1426       1.32
27      Camden            Oaklyn        426   6   1          1585       1.35
28      Camden        Pennsauken        427   6   1          1141       0.85
29      Camden         Pine Hill        428   8   1           950       1.13
30      Camden       Pine Valley        429   8   1         54818       1.28
31      Camden         Runnemede        430   5   1          1068       1.01
32      Camden         Somerdale        431   6   1          1369       0.96
33      Camden         Stratford        432   6   1          1012       0.88
34      Camden         Tavistock        433   6   1         31107       0.75
35      Camden          Voorhees        434   6   1          1447       0.80
36      Camden           Winslow        436   4   1           860       0.60
37      Camden         Woodlynne        437   5   1          1209       3.04
38  Gloucester          Deptford        802   5   1          1185       0.79
39  Gloucester    East Greenwich        803   3   1           823       0.34
40  Gloucester         Glassboro        806   3   1          1389       1.03
41  Gloucester         Greenwich        807   3   1          3074       1.43
42  Gloucester             Logan        809   3   1          2398       0.44
43  Gloucester            Monroe        811   4   1          1015       0.84
44  Gloucester     National Park        812   3   1          1253       0.92
45  Gloucester         Paulsboro        814   3   1          1469       1.61
46  Gloucester    Washington Twp        818   4   1           902       0.57
47  Gloucester           Wenonah        819   5   1          1168       0.65
48  Gloucester     West Deptford        820   3   1          1738       0.93
49  Gloucester         Westville        821   5   1          1499       1.33
50  Gloucester          Woodbury        822   5   1          1465       1.53
51  

In [10]:
b = b.rename(columns={'DLGS Code': 'DCA'})
b.query("DCA >400 & DCA <438")
#Doing the same type of subsetting here to make sure none of the Burlington County or Gloucester County townships from the 1st Congressional District are included

COUNTY     Municipality  DCA  LD  CD  BudgetTwenty  MTRTwenty
2   Camden          Audubon  401   5   1          1335       0.87
3   Camden     Audubon Park  402   5   1          1109       3.72
4   Camden       Barrington  403   5   1          1357       1.18
5   Camden         Bellmawr  404   5   1          1364       1.13
6   Camden           Berlin  405   8   1          1275       0.79
7   Camden       Berlin Twp  406   6   1          1901       1.20
8   Camden        Brooklawn  407   5   1          1980       1.68
9   Camden           Camden  408   5   1          2519       1.55
10  Camden      Cherry Hill  409   6   1          1044       0.48
11  Camden      Chesilhurst  410   4   1          2148       1.80
12  Camden        Clementon  411   4   1          1261       1.60
13  Camden     Collingswood  412   6   1          1420       0.98
14  Camden        Gibbsboro  413   6   1          1554       0.88
15  Camden  Gloucester City  414   5   1          1838       2.30
16  Camden   Gloucester Twp  415   4   1          1067       1.13
17  Camden   Haddon Heights  418   5   1          1151       0.72
18  Camden       Haddon Twp  416   6   1           967       0.65
19  Camden      Haddonfield  417   6   1          1722       0.47
20  Camden         Hi-Nella  419   6   1          1112       1.48
21  Camden   Laurel Springs  420   4   1          1767       1.64
22  Camden         Lawnside  421   5   1          1745       0.95
23  Camden       Lindenwold  422   4   1           969       1.67
24  Camden         Magnolia  423   5   1          1381       1.03
25  Camden    Merchantville  424   6   1          1358       1.25
26  Camden    Mount Ephraim  425   5   1          1426       1.32
27  Camden           Oaklyn  426   6   1          1585       1.35
28  Camden       Pennsauken  427   6   1          1141       0.85
29  Camden        Pine Hill  428   8   1           950       1.13
30  Camden      Pine Valley  429   8   1         54818       1.28
31  Camden        Runnemede  430   5   1          1068       1.01
32  Camden        Somerdale  431   6   1          1369       0.96
33  Camden        Stratford  432   6   1          1012       0.88
34  Camden        Tavistock  433   6   1         31107       0.75
35  Camden         Voorhees  434   6   1          1447       0.80
36  Camden          Winslow  436   4   1           860       0.60
37  Camden        Woodlynne  437   5   1          1209       3.04

In [11]:
c.query("DCA >400 & DCA <438")

OBJECTID         GEOID  POVUNIVERSE  POPUNDER2XPOV  LOW_INCOME_PCT  \
671       672  340076002001         1184            637       53.800676   
672       673  340076002002          777            316       40.669241   
673       674  340076004001         1611           1387       86.095593   
674       675  340076004002         1321            721       54.579864   
675       676  340076007001         1516            865       57.058047   
..        ...           ...          ...            ...             ...   
866       867  340076115003          101            101      100.000000   
867       868  340076115004          647            266       41.112828   
868       869  340076116001         1154            466       40.381282   
869       870  340076116003         1738           1069       61.507480   
870       871  340076116004          477             79       16.561845   

     TOTALPOP  NONHISPWHITE  TOTALMINORITY  MINORITY_PCT  TOTHH  ...  \
671      1184             0           1184    100.000000    446  ...   
672       777             0            777    100.000000    266  ...   
673      1611            32           1579     98.013656    761  ...   
674      1321             0           1321    100.000000    385  ...   
675      1516            98           1418     93.535620    465  ...   
..        ...           ...            ...           ...    ...  ...   
866       733           332            401     54.706685      0  ...   
867       647           631             16      2.472952    269  ...   
868      1216           901            315     25.904605    633  ...   
869      1738           503           1235     71.058688   1010  ...   
870       477           209            268     56.184486    217  ...   

       BG_TRIBAL  GEOID_COUNTYSUBDIVISION  COUNTY                  NAME  DCA  \
671  Block Group               3400710000  CAMDEN           Camden City  408   
672  Block Group               3400710000  CAMDEN           Camden City  408   
673  Block Group               3400710000  CAMDEN           Camden City  408   
674  Block Group               3400710000  CAMDEN           Camden City  408   
675  Block Group               3400710000  CAMDEN           Camden City  408   
..           ...                      ...     ...                   ...  ...   
866  Block Group               3400781740  CAMDEN      Winslow Township  436   
867  Block Group               3400781740  CAMDEN      Winslow Township  436   
868  Block Group               3400714260  CAMDEN  Collingswood Borough  412   
869  Block Group               3400714260  CAMDEN  Collingswood Borough  412   
870  Block Group               3400728740  CAMDEN       Haddon Township  416   

                    SPLIT_BG       SPLIT_MUN  \
671  Not a Split Block Group  Not Applicable   
672  Not a Split Block Group  Not Applicable   
673  Not a Split Block Group  Not Applicable   
674  Not a Split Block Group  Not Applicable   
675  Not a Split Block Group  Not Applicable   
..                       ...             ...   
866  Not a Split Block Group  Not Applicable   
867  Not a Split Block Group  Not Applicable   
868  Not a Split Block Group  Not Applicable   
869  Not a Split Block Group  Not Applicable   
870  Not a Split Block Group  Not Applicable   

                                 GLOBALID   Shape__Area Shape__Length  
671  7c187685-adaf-424b-b413-072360e69db0  1.119380e+07  22733.129504  
672  42b361a7-eb89-4449-a2a8-5405ce91645f  2.009601e+06   9261.088529  
673  c980b2af-12dc-4b56-a6e5-127683f29327  5.704404e+06   9551.308307  
674  9acad641-3dc9-4fde-82fb-5b9d97663e1e  3.577809e+06   8211.935538  
675  12a3e1f9-d223-4a90-98b7-bd722a661fce  1.270752e+07  14756.824896  
..                                    ...           ...           ...  
866  f5e56ff2-48ea-42b0-a533-0a9849add736  3.337829e+07  29839.803562  
867  9621a22f-2404-4ad7-b376-838f17192513  7.996054e+07  49676.614082  
868  fc4fd707-dd06-48ff-ae3c-e65f2f95b151  5.857543e+

In [12]:
#Let's do basic merge first, and then do Many:1 merge later
bc = pd.merge(b, c, how='left', on=['DCA'],indicator=True) #outer=keep all

In [13]:
bc._merge.value_counts()

both          250
left_only      16
right_only      0
Name: _merge, dtype: int64